In [1]:
# import necessary libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import gensim, logging, io, os, re, itertools

import lda_funcs # helper functions for LDA tuning

from gensim import corpora
from gensim.models.coherencemodel import CoherenceModel

In [2]:
# set up logging
logging.basicConfig(format='%(asctime)s : %(levelname)s : %(message)s', level=logging.INFO)
handler = logging.FileHandler('training_output.log')

# The handler above is somthing I needed with respect to logging.
# Gensim performs various calculations while training the LDA model that I am using, but the only way to see them
# is in the logging outputs.
# Specifically, I need to capture the perplexity values during training to verify that perplexity is decreasing.
# This metric is needed to compare models and to do hyperparameter tuning. 


# The following blog post was helpful to me in figure out how to make the log handler I needed.
# https://fangpenlin.com/posts/2012/08/26/good-logging-practice-in-python/

In [3]:
df = pd.read_csv('reviews_subset.csv', index_col=0)
df.head(2)

Unnamed: 0.1   ProductId          UserId   ProfileName  \
0             0  B000KV61FC  A1Y1YYH71TPYC6   thefinfan54   
1             1  B000KV61FC  A1SLLKDKCZ5IPL  C. Guariglia   

   HelpfulnessNumerator  HelpfulnessDenominator  Score        Time  \
0                     2                       2      5  1222905600   
1                     2                       2      2  1221091200   

                             Summary  \
0  The best dog toy I ever bought :)   
1           Buried Treasure Forever!   

                                                Text  \
0  I have two smaller dogs and they absolutely lo...   
1  The idea is basically a good one, however, my ...   

                         ...                          Valence Fit  \
0                        ...                             0.433204   
1                        ...                             0.728594   

                                        lemmas_clean  \
0  ['two', 'small', 'dog', 'absolutely', 'love', ...   
1  ['idea', 'basically', 'good', 'one', 'however'...   

                                      lemmas_vanilla  \
0  ['i', 'have', 'two', 'small', 'dog', 'and', 't...   
1  ['the', 'idea', 'be', 'basically', 'a', 'good'...   

                                       clean_vanilla  \
0  two small dog absolutely love tug jug many us ...   
1  idea basically good one however large papillon...   

                                    vanilla_stripped  \
0  two small dog absolutely love tug jug many us ...   
1  idea basically good one however large papillon...   

                                      coded_stripped  \
0  two small dog absolutely love GOODREVIEW tug j...   
1  idea basically good GOODREVIEW one however lar...   

                                    valence_stripped  \
0  two small dog absolutely love VGOODREVIEW tug ...   
1  idea basically good GOODREVIEW one however lar...   

                                     clean_vanilla_x  \
0  two small dog absolutely love tug jug many us ...   
1  idea basically good one however large papillon...   

                                       clean_coded_x  \
0  two small dog absolutely love GOODREVIEW tug j...   
1  idea basically good GOODREVIEW one however lar...   

                                     clean_valence_x  
0  two small dog absolutely love VGOODREVIEW tug ...  
1  idea basically good GOODREVIEW one however lar...  

[2 rows x 45 columns]

In [4]:
# get review counts for each product
review_counts = df['ProductId'].value_counts().sort_values()
review_counts.tail(12)

B002IEZJMA    487
B006MONQMC    491
B005ZBZLT4    506
B003GTR8IO    530
B005K4Q34S    541
B000NMJWZO    542
B0013A0QXC    542
B000KV61FC    556
B001EO5Q64    567
B0026RQTGE    630
Name: ProductId, dtype: int64

In [5]:
# get a couple product groups to work with - the 10 products with the largest number of reviews
top_ten = review_counts.tail(10).index.values

## LDA Model Grid Search & Tuning

For each of the input text types (vanilla, coded, and valence coded), first run an initial grid search with 50 or 80 training passes and either 6, 10, or 12 topics.

NOTE: grid search can take hours to run fully - don't run the below cells unless you actually want to perform the searching and tuning. The csv results files can simply be loaded in where noted below.

In [ ]:
# LOAD RESULTS
# load in the final results
vanilla_final_results = pd.read_csv('vanilla_final_results.csv')
vanilla_final_results.set_index('product', inplace=True)

coded_final_results = pd.read_csv('coded_final_results.csv')
coded_final_results.set_index('product', inplace=True)

valence_final_results = pd.read_csv('valence_final_results.csv')
valence_final_results.set_index('product', inplace=True)

### Vanilla Inputs Grid Search & Tuning

In [ ]:
# CAUTION - GRID SEARCH CAN TAKE MANY HOURS TO RUN
# ONLY RUN ON FIRST PASS
# create a dataframe to house the results of the model tuning from an initial grid search

vanilla_gs_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 
                                           'perplexity', 'topic diff', 'final perplexity', 'final topic diff', 
                                           'perplexity decreasing', 'coherence', 'top_n removed', 'n_above threshold'])

# for each of the top ten products, grid search over a combination of n_passes and n_topics 
# save the parameter combinations (and saved model) of the model with the highest coherence score
for product in top_ten:
    output = lda_funcs.tune_lda(df=df, product=product, n_passes=[50, 80], n_topics=[6, 8, 10, 12], save_path='vanilla_outputs',\
                      input_text='clean_vanilla', n_below=0, top_n=[2,10], n_above=[0.5, 1.0])
    vanilla_gs_results = lda_funcs.save_best(output, vanilla_gs_results, save_path="vanilla_outputs")

In [ ]:
vanilla_gs_results

In [ ]:
# RUN ONLY ON FIRST PASS
# save off the results with the best model (highest coherence) for each product
# examine the results
vanilla_gs_results.to_csv('vanilla_gs_results.csv')
vanilla_gs_results[['product','coherence', 'num_topics', 'passes']]

In [6]:
# LOAD RESULTS
vanilla_gs_results = pd.read_csv('vanilla_gs_results.csv')
vanilla_gs_results[['product','coherence', 'num_topics', 'passes', 'top_n removed', 'n_above threshold']]

product  coherence  num_topics  passes  top_n removed  n_above threshold
0  B002IEZJMA   0.511191          12      80              2                0.5
1  B006MONQMC   0.439355          12      50              2                0.5
2  B005ZBZLT4   0.479682           6      80              2                0.5
3  B003GTR8IO   0.413433           8      80              2                1.0
4  B005K4Q34S   0.446017          12      80              2                0.5
5  B0013A0QXC   0.473835           6      80              2                1.0
6  B000NMJWZO   0.497153           6      50              2                0.5
7  B000KV61FC   0.496802          10      80              2                1.0
8  B001EO5Q64   0.449167           8      80              2                1.0
9  B0026RQTGE   0.460886           6      80              2                1.0

Next, after reviewing the results of the initial grid search pass, and manually tune the models for each of the products to try to reach a threshold of 0.5 for the final model coherence. 

In [19]:
# run this cell for the products that needs further tuning
# increase or decrease the number of passes or topics depending on the best model found from previous results
output = lda_funcs.tune_lda(df=df, product='B005K4Q34S', n_passes=[80, 100], n_topics=[11, 12, 13, 14], save_path='vanilla_outputs',\
                  input_text='clean_vanilla', n_below=0, top_n=[2], n_above=[0.5])

2018-09-19 15:11:12,552 : INFO : adding document #0 to Dictionary(0 unique tokens: [])
2018-09-19 15:11:12,610 : INFO : built Dictionary(1824 unique tokens: ['dash', 'plain', 'chemical', 'definetly', 'way']...) from 541 documents (total 13224 corpus positions)
2018-09-19 15:11:12,616 : INFO : discarding 2 tokens: [('coffee', 254), ('cup', 243)]...
2018-09-19 15:11:12,623 : INFO : resulting dictionary: Dictionary(1822 unique tokens: ['dash', 'plain', 'chemical', 'definetly', 'way']...)
2018-09-19 15:11:12,629 : INFO : discarding 0 tokens: []...
2018-09-19 15:11:12,635 : INFO : keeping 1822 tokens which were in no less than 0 and no more than 270 (=50.0%) documents
2018-09-19 15:11:12,646 : INFO : resulting dictionary: Dictionary(1822 unique tokens: ['dash', 'plain', 'chemical', 'definetly', 'way']...)
2018-09-19 15:11:12,683 : INFO : storing corpus in Matrix Market format to /tmp/corpus.mm
2018-09-19 15:11:12,687 : INFO : saving sparse matrix to /tmp/corpus.mm
2018-09-19 15:11:12,689 : 

training LDA with 11 topics over 80 passes
removing top 2 words with 0.5 review freq threshold


2018-09-19 15:11:13,126 : INFO : merging changes from 180 documents into a model of 541 documents
2018-09-19 15:11:13,135 : INFO : topic #2 (0.091): 0.034*"cappuccino" + 0.024*"vanilla" + 0.019*"flavor" + 0.019*"french" + 0.019*"great" + 0.018*"keurig" + 0.017*"think" + 0.017*"love" + 0.015*"get" + 0.014*"order"
2018-09-19 15:11:13,137 : INFO : topic #6 (0.091): 0.028*"taste" + 0.020*"buy" + 0.017*"bad" + 0.017*"like" + 0.011*"k" + 0.010*"get" + 0.009*"need" + 0.009*"would" + 0.009*"great" + 0.009*"cappuccino"
2018-09-19 15:11:13,140 : INFO : topic #8 (0.091): 0.022*"taste" + 0.020*"like" + 0.018*"get" + 0.013*"would" + 0.013*"really" + 0.011*"cappuccino" + 0.011*"artificial" + 0.010*"try" + 0.009*"find" + 0.009*"station"
2018-09-19 15:11:13,144 : INFO : topic #3 (0.091): 0.024*"love" + 0.023*"sugar" + 0.021*"k" + 0.016*"buy" + 0.015*"caramel" + 0.015*"cappuccino" + 0.015*"one" + 0.013*"delicious" + 0.013*"find" + 0.012*"great"
2018-09-19 15:11:13,146 : INFO : topic #9 (0.091): 0.024*"

2018-09-19 15:11:14,438 : INFO : topic #10 (0.091): 0.040*"taste" + 0.037*"cappuccino" + 0.034*"would" + 0.026*"like" + 0.019*"deliver" + 0.018*"sweet" + 0.018*"flavor" + 0.015*"love" + 0.015*"full" + 0.014*"great"
2018-09-19 15:11:14,441 : INFO : topic #2 (0.091): 0.032*"grove" + 0.032*"square" + 0.026*"vanilla" + 0.023*"french" + 0.022*"cappuccino" + 0.021*"k" + 0.020*"great" + 0.018*"look" + 0.017*"price" + 0.017*"taste"
2018-09-19 15:11:14,445 : INFO : topic #0 (0.091): 0.031*"find" + 0.023*"need" + 0.017*"time" + 0.017*"love" + 0.015*"enjoy" + 0.013*"order" + 0.013*"amazon" + 0.013*"store" + 0.012*"drink" + 0.011*"cream"
2018-09-19 15:11:14,449 : INFO : topic diff=0.497703, rho=0.447214
2018-09-19 15:11:14,460 : INFO : -5.121 per-word bound, 34.8 perplexity estimate based on a held-out corpus of 1 documents with 18 words
2018-09-19 15:11:14,461 : INFO : PROGRESS: pass 1, at document #542/541
2018-09-19 15:11:14,468 : INFO : merging changes from 1 documents into a model of 541 docu

2018-09-19 15:11:15,281 : INFO : topic #5 (0.091): 0.245*"attention" + 0.047*"would" + 0.019*"artificial" + 0.013*"oil" + 0.012*"ingredient" + 0.012*"hydrogenate" + 0.010*"sucralose" + 0.010*"box" + 0.008*"contain" + 0.008*"partially"
2018-09-19 15:11:15,285 : INFO : topic #10 (0.091): 0.041*"taste" + 0.034*"cappuccino" + 0.030*"like" + 0.023*"great" + 0.022*"would" + 0.021*"love" + 0.019*"sweet" + 0.016*"k" + 0.016*"good" + 0.014*"flavor"
2018-09-19 15:11:15,290 : INFO : topic diff=0.330171, rho=0.377964
2018-09-19 15:11:15,299 : INFO : PROGRESS: pass 3, at document #360/541
2018-09-19 15:11:15,452 : INFO : merging changes from 180 documents into a model of 541 documents
2018-09-19 15:11:15,460 : INFO : topic #6 (0.091): 0.028*"sweet" + 0.021*"taste" + 0.019*"like" + 0.017*"get" + 0.015*"nice" + 0.015*"way" + 0.014*"something" + 0.013*"little" + 0.012*"small" + 0.011*"need"
2018-09-19 15:11:15,462 : INFO : topic #10 (0.091): 0.039*"taste" + 0.034*"like" + 0.033*"cappuccino" + 0.026*"l

...

2018-09-19 15:17:27,805 : INFO : topic #0 (0.071): 0.033*"find" + 0.023*"store" + 0.020*"pay" + 0.017*"let" + 0.016*"carry" + 0.015*"could" + 0.014*"amazon" + 0.014*"box" + 0.014*"stuff" + 0.013*"cider"
2018-09-19 15:17:27,810 : INFO : topic #7 (0.071): 0.027*"taste" + 0.025*"good" + 0.023*"like" + 0.023*"buy" + 0.022*"k" + 0.020*"sugar" + 0.016*"sweet" + 0.016*"great" + 0.015*"drink" + 0.015*"add"
2018-09-19 15:17:27,813 : INFO : topic #8 (0.071): 0.047*"artificial" + 0.032*"ingredient" + 0.026*"one" + 0.026*"box" + 0.024*"people" + 0.020*"oil" + 0.019*"would" + 0.018*"sucralose" + 0.017*"hydrogenate" + 0.016*"give"
2018-09-19 15:17:27,818 : INFO : topic diff=0.048213, rho=0.101535
2018-09-19 15:17:27,830 : INFO : -4.305 per-word bound, 19.8 perplexity estimate based on a held-out corpus of 1 documents with 18 words
2018-09-19 15:17:27,831 : INFO : PROGRESS: pass 93, at document #542/541
2018-09-19 15:17:27,837 : INFO : merging changes from 1 documents into a model of 541 documents
20

2018-09-19 15:17:28,449 : INFO : topic #1 (0.071): 0.341*"change" + 0.023*"review" + 0.022*"quite" + 0.020*"local" + 0.012*"able" + 0.012*"consider" + 0.008*"company" + 0.008*"cap" + 0.008*"version" + 0.007*"life"
2018-09-19 15:17:28,452 : INFO : topic #6 (0.071): 0.040*"taste" + 0.031*"sweet" + 0.024*"get" + 0.022*"lot" + 0.020*"like" + 0.020*"bad" + 0.019*"instant" + 0.019*"waste" + 0.019*"way" + 0.015*"money"
2018-09-19 15:17:28,455 : INFO : topic diff=0.049139, rho=0.100504
2018-09-19 15:17:28,464 : INFO : PROGRESS: pass 95, at document #360/541
2018-09-19 15:17:28,591 : INFO : merging changes from 180 documents into a model of 541 documents
2018-09-19 15:17:28,600 : INFO : topic #0 (0.071): 0.031*"find" + 0.022*"store" + 0.020*"pay" + 0.018*"let" + 0.016*"could" + 0.015*"amazon" + 0.015*"box" + 0.015*"stuff" + 0.015*"carry" + 0.014*"cider"
2018-09-19 15:17:28,602 : INFO : topic #12 (0.071): 0.333*"attention" + 0.021*"serve" + 0.016*"pleased" + 0.015*"flavorful" + 0.015*"fan" + 0.0

2018-09-19 15:17:29,225 : INFO : topic diff=0.047500, rho=0.100000
2018-09-19 15:17:29,235 : INFO : -4.304 per-word bound, 19.8 perplexity estimate based on a held-out corpus of 1 documents with 18 words
2018-09-19 15:17:29,237 : INFO : PROGRESS: pass 96, at document #542/541
2018-09-19 15:17:29,241 : INFO : merging changes from 1 documents into a model of 541 documents
2018-09-19 15:17:29,250 : INFO : topic #0 (0.071): 0.032*"find" + 0.022*"store" + 0.019*"pay" + 0.017*"let" + 0.015*"carry" + 0.015*"could" + 0.014*"amazon" + 0.014*"box" + 0.014*"stuff" + 0.012*"cider"
2018-09-19 15:17:29,253 : INFO : topic #7 (0.071): 0.027*"taste" + 0.025*"good" + 0.023*"like" + 0.023*"buy" + 0.022*"k" + 0.020*"sugar" + 0.016*"sweet" + 0.016*"great" + 0.015*"drink" + 0.015*"add"
2018-09-19 15:17:29,255 : INFO : topic #6 (0.071): 0.038*"taste" + 0.032*"sweet" + 0.025*"get" + 0.024*"lot" + 0.021*"like" + 0.020*"way" + 0.019*"bad" + 0.018*"instant" + 0.018*"waste" + 0.017*"usually"
2018-09-19 15:17:29,2

2018-09-19 15:17:30,007 : INFO : topic #3 (0.071): 0.034*"sugar" + 0.034*"fat" + 0.030*"calorie" + 0.025*"find" + 0.023*"high" + 0.016*"fit" + 0.015*"instead" + 0.015*"something" + 0.014*"drink" + 0.014*"reasonable"
2018-09-19 15:17:30,010 : INFO : topic #8 (0.071): 0.046*"artificial" + 0.031*"ingredient" + 0.027*"one" + 0.025*"people" + 0.025*"box" + 0.020*"oil" + 0.018*"would" + 0.017*"hydrogenate" + 0.016*"sucralose" + 0.016*"get"
2018-09-19 15:17:30,012 : INFO : topic #12 (0.071): 0.334*"attention" + 0.021*"serve" + 0.016*"pleased" + 0.015*"flavorful" + 0.015*"fan" + 0.011*"syrup" + 0.010*"wow" + 0.007*"corn" + 0.007*"vegetable" + 0.007*"trans"
2018-09-19 15:17:30,016 : INFO : topic #4 (0.071): 0.134*"flavor" + 0.115*"enjoyable" + 0.070*"hazelnut" + 0.067*"try" + 0.065*"cappuccino" + 0.065*"favorite" + 0.065*"think" + 0.064*"would" + 0.062*"also" + 0.059*"deliver"
2018-09-19 15:17:30,020 : INFO : topic diff=0.044416, rho=0.099015
2018-09-19 15:17:30,029 : INFO : PROGRESS: pass 98, 

2018-09-19 15:17:30,641 : INFO : topic #13 (0.071): 0.036*"hot" + 0.033*"mix" + 0.029*"powder" + 0.028*"cocoa" + 0.023*"ground" + 0.021*"chocolate" + 0.021*"filter" + 0.012*"notice" + 0.010*"bottom" + 0.009*"less"
2018-09-19 15:17:30,645 : INFO : topic #4 (0.071): 0.136*"flavor" + 0.120*"enjoyable" + 0.070*"hazelnut" + 0.068*"try" + 0.066*"cappuccino" + 0.066*"favorite" + 0.066*"think" + 0.065*"would" + 0.064*"also" + 0.061*"deliver"
2018-09-19 15:17:30,649 : INFO : topic #7 (0.071): 0.027*"taste" + 0.025*"good" + 0.023*"like" + 0.023*"buy" + 0.022*"k" + 0.020*"sugar" + 0.016*"sweet" + 0.016*"great" + 0.015*"drink" + 0.015*"add"
2018-09-19 15:17:30,652 : INFO : topic diff=0.092438, rho=0.098533
2018-09-19 15:17:30,885 : INFO : saving LdaState object under ./vanilla_outputs/B005K4Q34S_14_100_2_0.5.state, separately None
2018-09-19 15:17:30,889 : INFO : saved ./vanilla_outputs/B005K4Q34S_14_100_2_0.5.state
2018-09-19 15:17:30,892 : INFO : saving LdaModel object under ./vanilla_outputs/B0

In [20]:
# view the outputs
output

chunk  coherence  final perplexity  final topic diff  \
0  180.333333   0.403736              18.5          0.055667   
0  180.333333   0.406111              18.4          0.050004   
0  180.333333   0.446017              18.4          0.083701   
0  180.333333   0.444515              19.6          0.050219   
0  180.333333   0.442644              19.6          0.090687   
0  180.333333   0.436657              20.7          0.047832   
0  180.333333   0.409318              20.7          0.084216   
0  180.333333   0.410312              19.7          0.046822   

   n_above threshold num_topics passes  \
0                0.5         11     80   
0                0.5         11    100   
0                0.5         12     80   
0                0.5         12    100   
0                0.5         13     80   
0                0.5         13    100   
0                0.5         14     80   
0                0.5         14    100   

                                     per-word bounds  \
0  {0: -9.664, 1: -5.121, 2: -4.674, 3: -4.574, 4...   
0  {0: -9.664, 1: -5.121, 2: -4.674, 3: -4.574, 4...   
0  {0: -9.74, 1: -5.259, 2: -4.898, 3: -4.695, 4:...   
0  {0: -9.74, 1: -5.259, 2: -4.898, 3: -4.695, 4:...   
0  {0: -9.965, 1: -5.386, 2: -4.912, 3: -4.722, 4...   
0  {0: -9.965, 1: -5.386, 2: -4.912, 3: -4.722, 4...   
0  {0: -10.087, 1: -5.187, 2: -4.796, 3: -4.655, ...   
0  {0: -10.087, 1: -5.187, 2: -4.796, 3: -4.655, ...   

                                          perplexity perplexity decreasing  \
0  {0: 811.1, 1: 34.8, 2: 25.5, 3: 23.8, 4: 23.0,...                  True   
0  {0: 811.1, 1: 34.8, 2: 25.5, 3: 23.8, 4: 23.0,...                  True   
0  {0: 855.4, 1: 38.3, 2: 29.8, 3: 25.9, 4: 24.3,...                  True   
0  {0: 855.4, 1: 38.3, 2: 29.8, 3: 25.9, 4: 24.3,...                  True   
0  {0: 999.7, 1: 41.8, 2: 30.1, 3: 26.4, 4: 24.7,...                  True   
0  {0: 999.7, 1: 41.8, 2: 30.1, 3: 26.4, 4: 24.7,...                  True   
0  {0: 1088.0, 1: 36.4, 2: 27.8, 3: 25.2, 4: 24.0...                  True   
0  {0: 1088.0, 1: 36.4, 2: 27.8, 3: 25.2, 4: 24.0...                  True   

                         ...                          \
0                        ...                           
0                        ...                           
0                        ...                           
0                        ...                           
0                        ...                           
0                        ...                           
0                        ...                           
0                        ...                           

                                            topic 13  \
0                                                NaN   
0                                                NaN   
0                                                NaN   
0                                                NaN   
0                                                NaN   
0                                                NaN   
0  [(hot, 0.036293037), (mix, 0.032982875), (powd...   
0  [(hot, 0.036179483), (mix, 0.03305744), (powde...   

                                             topic 2  \
0  [(square, 0.08244736), (grove, 0.08244736), (v...   
0  [(square, 0.084259085), (grove, 0.08425907), (...   
0  [(empty, 0.02158351), (compare, 0.01840706), (...   
0  [(empty, 0.021608133), (compare, 0.018551677),...   
0  [(grove, 0.031024206), (square, 0.031024206), ...   
0  [(grove, 0.031252004), (square, 0.031252004), ...   
0  [(nice, 0.050706305), (treat, 0.03097094), (pi...   
0  [(nice, 0.05091759), (treat, 0.031106874), (pi...   

                                             topic 3  \
0  [(fat, 0.039966755), (free, 0.01767171), (suga...   
0  [(fat, 0.039844457), (free, 0.017737217), (sug...   
0  [(full, 0.2942976), (catch, 0.29330018), (dark...   
0  [(full, 0.2919706), (catch, 0.29092598), (dark...   
0  [(sugar, 0.034576904), (fat, 0.033339214), (wi

In [ ]:
output.iloc[3]['topic 4']

In [ ]:
# if the result is an improvement, run this cell to save it
# save off the updated results dataframe
vanilla_gs_results = lda_funcs.save_best(output, vanilla_gs_results, save_path="vanilla_outputs")
vanilla_gs_results.to_csv('vanilla_gs_results.csv')

In [ ]:
# finally, save off the best results into a final output dataframe
# create a df to collect the best models from all grid search tuning efforts
# save it off to a csv
vanilla_final_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 'perplexity', 'topic diff',
                                  'final perplexity', 'final topic diff', 'perplexity decreasing', 'coherence'])

for product in top_ten:
    output = vanilla_gs_results[vanilla_gs_results['product']==product]
    vanilla_final_results = lda_funcs.save_best(output, vanilla_final_results, save_path="vanilla_outputs")

vanilla_final_results.to_csv('vanilla_final_results.csv')

In [ ]:
# LOAD RESULTS
# load in the final results
vanilla_final_results = pd.read_csv('vanilla_final_results.csv')
vanilla_final_results.set_index('product', inplace=True)
vanilla_final_results[['coherence', 'num_topics', 'passes']]

The results above show that success with the vanilla review (i.e., no codewords, just clean text) was pretty poor - I was not able to achieve the 0.5 goal threshold with any of the products. 

### Coded Inputs Grid Search & Tuning

In [ ]:
# CAUTION - GRID SEARCH CAN TAKE MANY HOURS TO RUN
# ONLY RUN ON FIRST PASS
# create a dataframe to house the results of the model tuning from an initial grid search

coded_gs_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 'perplexity', 'topic diff',
                                  'final perplexity', 'final topic diff', 'perplexity decreasing', 'coherence'])

# for each of the top ten products, grid search over a combination of n_passes and n_topics 
# save the parameter combinations (and saved model) of the model with the highest coherence score
for product in top_ten:
    output = lda_funcs.tune_lda(df=df, product=product, n_passes=[50, 80], n_topics=[6, 10, 12], save_path='coded_outputs',\
                      input_text='clean_coded')
    coded_gs_results = lda_funcs.save_best(output, coded_gs_results, save_path="coded_outputs")

In [ ]:
# RUN ONLY ON FIRST PASS
# save off the results with the best model (highest coherence) for each product
# examine the results
coded_gs_results.to_csv('coded_gs_results.csv')
coded_gs_results[['product','coherence', 'num_topics', 'passes']]

In [ ]:
# LOAD RESULTS
coded_gs_results = pd.read_csv('coded_gs_results.csv')
coded_gs_results[['product','coherence', 'num_topics', 'passes']]

Next, after reviewing the results of the initial grid search pass, and manually tune the models for each of the products to try to reach a threshold of 0.5 for the final model coherence. 

In [ ]:
# run this cell for the product that needs further tuning
output = lda_funcs.tune_lda(df=df, product='B0026RQTGE', n_passes=[80, 100], n_topics=[6, 8, 14], save_path='coded_outputs',\
                  input_text='clean_coded')

In [ ]:
# view the outputs
output

In [ ]:
# if the result is an improvement, run this cell to save it
# save off the updated results dataframe
coded_gs_results = lda_funcs.save_best(output, coded_gs_results, save_path="coded_outputs")
coded_gs_results.to_csv('coded_gs_results.csv')

In [ ]:
# finally, save off the best results into a final output dataframe
# create a df to collect the best models from all grid search tuning efforts
# save it off to a csv
coded_final_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 'perplexity', 'topic diff',
                                  'final perplexity', 'final topic diff', 'perplexity decreasing', 'coherence'])

for product in top_ten:
    output = coded_gs_results[coded_gs_results['product']==product]
    coded_final_results = lda_funcs.save_best(output, coded_final_results, save_path="coded_outputs")

coded_final_results.to_csv('coded_final_results.csv')

In [ ]:
# LOAD RESULTS
# load in the final results
coded_final_results = pd.read_csv('coded_final_results.csv')
coded_final_results.set_index('product', inplace=True)
coded_final_results[['coherence', 'num_topics', 'passes']]

Using the coded review (i.e., with "GOODREVIEW" and "BADREVIEW" inserted following each positive or negative word), the coherence results are somewhat better than the uncoded reviews.

### Valence Coded Inputs Grid Search & Tuning

In [ ]:
# CAUTION - GRID SEARCH CAN TAKE MANY HOURS TO RUN
# ONLY RUN ON FIRST PASS
# create a dataframe to house the results of the model tuning from an initial grid search

valence_gs_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 'perplexity', 'topic diff',
                                  'final perplexity', 'final topic diff', 'perplexity decreasing', 'coherence'])

# for each of the top ten products, grid search over a combination of n_passes and n_topics 
# save the parameter combinations (and saved model) of the model with the highest coherence score
for product in top_ten:
    output = lda_funcs.tune_lda(df=df, product=product, n_passes=[50, 80], n_topics=[6, 10, 12], save_path='valence_outputs',\
                      input_text='clean_valence')
    valence_gs_results = lda_funcs.save_best(output, valence_gs_results, save_path="valence_outputs")

In [ ]:
# RUN ONLY ON FIRST PASS
# save off the results with the best model (highest coherence) for each product
# examine the results
valence_gs_results.to_csv('valence_gs_results.csv')
valence_gs_results[['product','coherence', 'num_topics', 'passes']]

In [ ]:
# LOAD RESULTS
valence_gs_results = pd.read_csv('valence_gs_results.csv')
valence_gs_results[['product','coherence', 'num_topics', 'passes']]

Next, after reviewing the results of the initial grid search pass, and manually tune the models for each of the products to try to reach a threshold of 0.5 for the final model coherence. 

In [ ]:
# run this cell for the product that needs further tuning
output = lda_funcs.tune_lda(df=df, product='B0026RQTGE', n_passes=[80], n_topics=[13, 15], save_path='valence_outputs',\
                  input_text='clean_valence')

In [ ]:
# view the outputs
output

In [ ]:
# if the result is an improvement, run this cell to save it
# save off the updated results dataframe
valence_gs_results = lda_funcs.save_best(output, valence_gs_results, save_path="valence_outputs")
valence_gs_results.to_csv('valence_gs_results.csv')

In [ ]:
# finally, save off the best results into a final output dataframe
# create a df to collect the best models from all grid search tuning efforts
# save it off to a csv
valence_final_results = pd.DataFrame(columns=['product', 'num_topics', 'chunk', 'passes', 'per-word bounds', 'perplexity', 'topic diff',
                                  'final perplexity', 'final topic diff', 'perplexity decreasing', 'coherence'])

for product in top_ten:
    output = valence_gs_results[valence_gs_results['product']==product]
    valence_final_results = lda_funcs.save_best(output, valence_final_results, save_path="valence_outputs")

valence_final_results.to_csv('valence_final_results.csv')

In [ ]:
# LOAD RESULTS
# load in the final results
valence_final_results = pd.read_csv('valence_final_results.csv')
valence_final_results.set_index('product', inplace=True)
valence_final_results[['coherence', 'num_topics', 'passes']]

### Initial Visualizations

In [ ]:
from nltk.collocations import BigramAssocMeasures, TrigramAssocMeasures, QuadgramCollocationFinder, BigramCollocationFinder, TrigramCollocationFinder
from nltk import word_tokenize, FreqDist, bigrams

In [ ]:
from bokeh.plotting import figure, show, output_notebook
from bokeh.models import ColumnDataSource, LabelSet, Jitter, HoverTool
from bokeh.palettes import GnBu3, OrRd3
from bokeh.core.properties import value
from bokeh.transform import dodge, jitter
from bokeh.layouts import gridplot

output_notebook()

In [ ]:
vanilla_coherence = vanilla_final_results['coherence']
coded_coherence = coded_final_results['coherence']
valence_coherence = valence_final_results['coherence']
vanilla_ts = vanilla_final_results['num_topics']
coded_ts = coded_final_results['num_topics']
valence_ts = valence_final_results['num_topics']

data_coherence = {'products' : top_ten,
        'vanilla'   : vanilla_coherence,
        'coded'   : coded_coherence,
        'valence'   : valence_coherence}

source_coherence = ColumnDataSource(data=data_coherence)

data_topics = {'products' : top_ten,
        'vanilla'   : vanilla_ts,
        'coded'   : coded_ts,
        'valence'   : valence_ts}

source_topics = ColumnDataSource(data=data_topics)

In [ ]:
p = figure(x_range=top_ten, y_range=(0, 0.7), plot_height=350, title="Coherence by Product",
           toolbar_location=None, tools="")

p.vbar(x=dodge('products', -0.25, range=p.x_range), top='vanilla', width=0.2, source=source_coherence,
       color="#c9d9d3", legend=value("Vanilla Reviews"))

p.vbar(x=dodge('products',  0.0,  range=p.x_range), top='coded', width=0.2, source=source_coherence,
       color="#718dbf", legend=value("Coded Reviews"))

p.vbar(x=dodge('products',  0.25, range=p.x_range), top='valence', width=0.2, source=source_coherence,
       color="#e84d60", legend=value("Valence Coded Reviews"))

p.x_range.range_padding = 0.1
p.xgrid.grid_line_color = None
p.legend.location = "top_left"
p.legend.orientation = "horizontal"
p.xaxis.major_label_orientation = 0.75

show(p)

Coded reviews appear to have the best general performance as far as coherence goes: for all but 4 of the 10 products, the average topic coherence is highest when using the coded reviews. 

In [ ]:
p = figure(x_range=top_ten, y_range=(0, 20), plot_height=350, title="Number of Topics by Product",
           toolbar_location=None, tools="")

p.vbar(x=dodge('products', -0.25, range=p.x_range), top='vanilla', width=0.2, source=source_topics,
       color="#c9d9d3", legend=value("Vanilla Reviews"))

p.vbar(x=dodge('products',  0.0,  range=p.x_range), top='coded', width=0.2, source=source_topics,
       color="#718dbf", legend=value("Coded Reviews"))

p.vbar(x=dodge('products',  0.25, range=p.x_range), top='valence', width=0.2, source=source_topics,
       color="#e84d60", legend=value("Valence Coded Reviews"))

p.x_range.range_padding = 0.1
p.xgrid.grid_line_color = None
p.legend.location = "top_left"
p.legend.orientation = "horizontal"
p.xaxis.major_label_orientation = 0.75

show(p)

There are no clear patterns in terms of the optimal number of topics found in the grid search for each input text type, but it is interesting to note that for some of the products the number of topics varies quite widely between the different input types. 

## Topic Quality Evaluation

Next, I'll dig a little deeper into the individual topics created by the LDA models for each product, and look at the distribution of reviews amongst the topics discovered. 

### Topic Assignment
Firts, how are the reviews for each product distributed among the topics discovered?

In [ ]:
import topic_dist

In [ ]:
df = pd.read_csv('reviews_subset.csv')

In [ ]:
for product in top_ten:
    topic_dist.assign_topics(df, product, vanilla_final_results, 'vanilla_outputs', 'clean_vanilla', 'Vanilla')
    topic_dist.assign_topics(df, product, coded_final_results, 'coded_outputs', 'clean_coded', 'Coded')
    topic_dist.assign_topics(df, product, valence_final_results, 'valence_outputs', 'clean_valence', 'Valence')

In [ ]:
# save off the updated dataframe
df[['Vanilla Topic', 'Coded Topic', 'Valence Topic']] = df[['Vanilla Topic', 'Coded Topic', 'Valence Topic']].astype(int)
df.to_csv('reviews_subset.csv')

In [ ]:
for product in top_ten:
    grid = topic_dist.plot_topic_distribution(df, product)
    show(grid)

For many of the products, regardless of the input text type used, the majority of reviews fall into one or two topics. This is the sort of class imbalance problem that would present problems for any classification exercise, as would the fact that the reviews in the dataset are overwhelmingly positive. 

However, it also appears that in many cases, the coded input text reviews have the most severe review concentration - that is, there is greater distribution amongst topics with the vanilla and the valence coded datasets. This could mean that the encoding has worked the opposite way I want it to. In using topic modeling, I am hoping to tease out various topic themes within the review set. Perhaps adding the simple codewords has simply resulted in topics that are mostly composed of negative or positive words. This means I need to further investigate the quality of the topics produced. 

### Topic Quality 

In [ ]:
import topic_funcs

First, I need to collect some information about each of the topics that will let me assess the quality of the topics, including:
* the number of reviews from that dataset that were classified into that topic
* the topic coherence
* the 'top' (most frequently appearing) words in the topic
* the most representative review (review in the dataset with the highest probability of having been generated by this topic model)
* the probability value for that review
* top bigrams and trigrams from the reviews classified to this topic, both by raw frequency as well as a measure of information (using PMI here)

In [ ]:
vanilla_topic_data = pd.DataFrame(columns = ['product', 'topic', 'review_count', 'topic_coherence', 'top_words',
                                            'best_review', 'best_review_fit', 'top_bigrams_pmi','top_bigrams_freq',
                                            'top_trigrams_pmi', 'top_trigrams_freq'])
for product in top_ten:
    stage_data = topic_funcs.get_topic_data(product, df, vanilla_final_results, 
                                            'clean_vanilla', 'vanilla_outputs', "Vanilla")
    vanilla_topic_data = pd.concat([vanilla_topic_data, stage_data])
    del stage_data

vanilla_topic_data.to_csv("vanilla_topic_data.csv")

In [ ]:
coded_topic_data = pd.DataFrame(columns = ['product', 'topic', 'review_count', 'topic_coherence', 'top_words',
                                            'best_review', 'best_review_fit', 'top_bigrams_pmi','top_bigrams_freq',
                                            'top_trigrams_pmi', 'top_trigrams_freq'])
for product in top_ten:
    stage_data = topic_funcs.get_topic_data(product, df, coded_final_results, 
                                            'clean_coded', 'coded_outputs', "Coded")
    coded_topic_data = pd.concat([coded_topic_data, stage_data])
    del stage_data

coded_topic_data.to_csv("coded_topic_data.csv")

In [ ]:
valence_topic_data = pd.DataFrame(columns = ['product', 'topic', 'review_count', 'topic_coherence', 'top_words',
                                            'best_review', 'best_review_fit', 'top_bigrams_pmi','top_bigrams_freq',
                                            'top_trigrams_pmi', 'top_trigrams_freq'])
for product in top_ten:
    stage_data = topic_funcs.get_topic_data(product, df, valence_final_results, 
                                            'clean_valence', 'valence_outputs', "Valence")
    valence_topic_data = pd.concat([valence_topic_data, stage_data])
    del stage_data

valence_topic_data.to_csv("valence_topic_data.csv")

In [ ]:
vanilla_topic_data = pd.read_csv("vanilla_topic_data.csv")
coded_topic_data = pd.read_csv("coded_topic_data.csv")
valence_topic_data = pd.read_csv("valence_topic_data.csv")

In [ ]:
from bokeh.plotting import figure, output_file, show
from bokeh.models import Range1d, LinearAxis

In [ ]:
def construct_plot(topic_data, product, encoding_type):
    data = topic_data[topic_data['product']==product]
    data.sort_values(ascending=False, axis=0, by='review_count', inplace=True) 
    x = ["Topic {}".format(t) for t in data['topic'].values]
    y = data['review_count']
    y2 = data['topic_coherence']

    p = figure(x_range=x, y_range=(0,550), plot_height=325, plot_width=325, toolbar_location=None,
               title = "{} Reviews: Product {}".format(encoding_type, product))
    

    p.vbar(x=x, top=y, width=0.9)
    p.yaxis.axis_label = "Review Count"
    p.extra_y_ranges = {"Topic Coherence": Range1d(start=0, end=1)}
    p.line(x=x, y=y2, color='red', y_range_name="Topic Coherence")
    p.add_layout(LinearAxis(y_range_name="Topic Coherence", axis_label='Topic Coherence'), 'right')
    p.xaxis.major_label_orientation = 0.75
    return p

In [ ]:
for product in top_ten:
    
    l = construct_plot(vanilla_topic_data, product, "Vanilla")
    c = construct_plot(coded_topic_data, product, 'Coded')
    r = construct_plot(valence_topic_data, product, 'Valence')
    grid = gridplot([[l, c, r]])
    show(grid)

Some observations about these plots:
* topic coherence typically appears to drop off as there are fewer reviews assigned to that topic
* there is also typically a drop in coherence after the top 1-3 topics (by # of reviews)
* as previously observed, there aren't any striking differences in the coherence measures between different text input types

In [ ]:
for product in top_ten[4:5]:
    print('Product {}'.format(product))
    print("Vanilla Reviews")
    vandata = vanilla_topic_data[vanilla_topic_data['product']==product]
    for topic in vandata['topic'].unique():
        print("Topic {}".format(topic))
        print("Reviews: {}".format(vandata.iloc[topic, 2]))
        print("Topic Coherence: {}".format(vandata.iloc[topic, 3]))
        print("Top Words: {}".format(vandata.iloc[topic, 4]))
        print("Best Review, fit {}: {}".format(vandata.iloc[topic, 6], 
                                               vandata.iloc[topic, 5]))
        print()

In [ ]:
vandata

In [ ]:
for product in top_ten:
    data = vanilla_topic_data[vanilla_topic_data['product']==product]
    #y = data['topic coherence']
    #x = data['best review fit']
    
    # for display purposes, take the log of the review count so the chart is visually readable
    data['review_count_transformed'] = np.log(data['review_count'].astype(int))*10
    
    source = ColumnDataSource(data)
    p = figure(x_range=(0,1.2), y_range=(0,1.2), plot_height=400, plot_width=400)
    p.circle(x='topic_coherence', y='best_review_fit', size='review_count_transformed', source=source, line_color="white")
    p.yaxis.axis_label="Topic Coherence"
    p.xaxis.axis_label="Best Review Fit"
    
    p.add_tools(HoverTool(tooltips=[("Topic","@topic"), ("Reviews","@review_count"), ("Bigrams","@top_bigrams_pmi"),
                                   ("Trigrams",'@top_trigrams_pmi')]))

    show(p)

In [ ]:
import scipy

In [ ]:
vanilla_topic_data